In [1]:
link1 = 'http://people.brunel.ac.uk/~mastjjb/jeb/orlib/files/cap82.txt'
link2 = 'http://people.brunel.ac.uk/~mastjjb/jeb/orlib/files/cap113.txt'
import numpy as np
import gurobipy as gp
from gurobipy import GRB

In [2]:
# define function to download data
def load_data(url, filename):
    import urllib.request
    response = urllib.request.urlretrieve(url,filename)
    file = open(filename,'r')
    return file

In [3]:
file = load_data(link2, 'cap113.txt')
data = file.readlines()

In [4]:
[locations, customers] = [int(x) for x in data[0].split(' ')[1:-1]]
capacity = []
fixcost = []
for i in range(locations):
    [c, f] = [float(x) for x in data[i+1].split(' ')[1:-1]]
    capacity.append(c)
    fixcost.append(f)
demand = []
varcost = np.zeros((locations,customers))
for j in range(customers):
    demand.append(float(data[j*9 + (1+locations)].split(' ')[1]))
    v = list(np.concatenate([data[j*9 + (1+locations+t)].split(' ')[1:-1] for t in range(1,9)]))
    for i in range(locations):
        varcost[i,j] = float(v[i])/demand[j] #cost of allocating demand of j to warehouse i per unit
        
        
print(locations)
print(customers)
print(capacity)
print(fixcost)
print(demand)
print(varcost)

bigM = min(np.max(capacity), sum(demand))
bigM

50
50
[5000.0, 5000.0, 5000.0, 5000.0, 5000.0, 5000.0, 5000.0, 5000.0, 5000.0, 5000.0, 5000.0, 5000.0, 5000.0, 5000.0, 5000.0, 5000.0, 5000.0, 5000.0, 5000.0, 5000.0, 5000.0, 5000.0, 5000.0, 5000.0, 5000.0, 5000.0, 5000.0, 5000.0, 5000.0, 5000.0, 5000.0, 5000.0, 5000.0, 5000.0, 5000.0, 5000.0, 5000.0, 5000.0, 5000.0, 5000.0, 5000.0, 5000.0, 5000.0, 5000.0, 5000.0, 5000.0, 5000.0, 5000.0, 5000.0, 5000.0]
[17500.0, 17500.0, 17500.0, 17500.0, 17500.0, 17500.0, 17500.0, 17500.0, 17500.0, 17500.0, 17500.0, 17500.0, 17500.0, 17500.0, 17500.0, 17500.0, 17500.0, 17500.0, 17500.0, 17500.0, 17500.0, 17500.0, 0.0, 17500.0, 17500.0, 17500.0, 17500.0, 17500.0, 17500.0, 17500.0, 17500.0, 17500.0, 17500.0, 17500.0, 17500.0, 17500.0, 17500.0, 17500.0, 17500.0, 17500.0, 17500.0, 17500.0, 17500.0, 17500.0, 17500.0, 17500.0, 17500.0, 17500.0, 17500.0, 17500.0]
[146.0, 87.0, 672.0, 1337.0, 31.0, 559.0, 2370.0, 1089.0, 33.0, 32.0, 5495.0, 904.0, 1466.0, 143.0, 615.0, 564.0, 226.0, 3016.0, 253.0, 195.0, 38.

5000.0

In [5]:
def subproblem(model, where):
    if where == GRB.Callback.MIPSOL:
        v_y = model.cbGetSolution(model._y)
        #print(v_y)
        LB = model.cbGetSolution(model._z)
        print('Current LB: ', LB, '\n')
        print(model.cbGet(GRB.Callback.MIPSOL_OBJBND))
        print(model.cbGet(GRB.Callback.MIPSOL_OBJBST))
        
        bsp = gp.Model("Subproblem") 
        x = {}
        for i in range(locations):
            for j in range(customers):
                x[i,j] = bsp.addVar(obj=varcost[i,j])
        
        #unserved demand
        s = {}
        add_cost = np.max(fixcost)*2
        for j in range(customers):
            s[j] = bsp.addVar(obj = add_cost)
        
        demand_constr = {} 
        for j in range(customers):
            demand_constr[j] = bsp.addConstr(sum(x[i,j] for i in range(locations)) + s[j] >= demand[j])
        
        log_constr = {}
        for i in range(locations):
            log_constr[i] = bsp.addConstr(sum(x[i,j] for j in range(customers)) <= v_y[i]* bigM)
        
        cap_constr = {}
        for i in range(locations):
            cap_constr[i] = bsp.addConstr(sum(x[i,j] for j in range(customers)) <= capacity[i])
        
        bsp.optimize()

        
        
        #update ub and lb
        fc = 0
        for i in range(locations):
            if sum(round(x[i,j].x) for j in range(customers)) > 0:
                fc+=fixcost[i]
        
        if bsp.objVal + fc > model.cbGet(GRB.Callback.MIPSOL_OBJBND):
            v = np.zeros(customers) #dual of demand constraints
            for j in range(customers):
                v[j] = demand_constr[j].pi #get dual value
            
            w = np.zeros(locations) #dual of logical constraints
            for i in range(locations):
                w[i] = log_constr[i].pi
            
            u = np.zeros(locations) #dual of capacity constraints
            for i in range(locations):
                u[i] = cap_constr[i].pi
            
            cm = np.zeros(locations) #coefficient of y in master problem
            for i in range(locations):
                cm[i] = fixcost[i]+ bigM*w[i] 
            

            model.cbLazy(model._z  >= sum(demand[j] * v[j] for j in range(customers)) +   
                         sum(capacity[i] * u[i] for i in range(locations)) + 
                         sum(cm[i] * model._y[i] for i in range(locations)))

        
        # save result of x from subproblem
        global transport
        for i in range(locations):
            for j in range(customers):
                transport[i,j] = x[i,j].x
        #print([transport[locations-1][j] for j in range(customers)])
        #print(bsp.objVal)

        bsp.dispose()
                       


In [6]:
transport = np.zeros((locations, customers)) # to save result of x from subproblem
# Masterproblem
                     
m = gp.Model("Benders Masterproblem")

y = {}
z = m.addVar(obj=1)                                                                           
for i in range(locations):
    y[i] = m.addVar(vtype=GRB.BINARY)
    

m.Params.lazyConstraints = 1
m._y = y
m._z = z
m.Params.TimeLimit = 1800
m.optimize(subproblem)
    
    
print("Objective: " + str(m.objVal))

print("Solution:")
import pandas as pd
index = ['Source ' + str(x+1) for x in range(locations)]
columns = ['Customer ' + str(x+1) for x in range(customers)]

solution = pd.DataFrame(index=index, columns=columns+['y'])

for i in range(locations):
    for j in range(customers):
        solution.iloc[i,j] = transport[i,j]
    solution.iloc[i,customers] = y[i].x

print(solution)


Using license file C:\Users\hadao\gurobi.lic
Academic license - for non-commercial use only
Changed value of parameter lazyConstraints to 1
   Prev: 0  Min: 0  Max: 1  Default: 0
Changed value of parameter TimeLimit to 1800.0
   Prev: inf  Min: 0.0  Max: inf  Default: inf
Gurobi Optimizer version 9.0.2 build v9.0.2rc0 (win64)
Optimize a model with 0 rows, 51 columns and 0 nonzeros
Model fingerprint: 0x222d02f8
Variable types: 1 continuous, 50 integer (50 binary)
Coefficient statistics:
  Matrix range     [0e+00, 0e+00]
  Objective range  [1e+00, 1e+00]
  Bounds range     [1e+00, 1e+00]
  RHS range        [0e+00, 0e+00]
Current LB:  0.0 

-1e+100
0.0
Gurobi Optimizer version 9.0.2 build v9.0.2rc0 (win64)
Optimize a model with 150 rows, 2550 columns and 7550 nonzeros
Model fingerprint: 0x833f6674
Coefficient statistics:
  Matrix range     [1e+00, 1e+00]
  Objective range  [1e+00, 4e+04]
  Bounds range     [0e+00, 0e+00]
  RHS range        [3e+01, 1e+04]
Presolve removed 150 rows and 2550

Optimize a model with 150 rows, 2550 columns and 7550 nonzeros
Model fingerprint: 0xdb81591b
Coefficient statistics:
  Matrix range     [1e+00, 1e+00]
  Objective range  [1e+00, 4e+04]
  Bounds range     [0e+00, 0e+00]
  RHS range        [3e+01, 1e+04]
Presolve removed 71 rows and 1050 columns
Presolve time: 0.01s
Presolved: 79 rows, 1500 columns, 2950 nonzeros

Iteration    Objective       Primal Inf.    Dual Inf.      Time
       0    0.0000000e+00   7.214625e+03   0.000000e+00      0s
      55    7.0189140e+05   0.000000e+00   0.000000e+00      0s

Solved in 55 iterations and 0.01 seconds
Optimal objective  7.018914000e+05
H    0     0                    1191891.4000 626456.433  47.4%     -    0s
Current LB:  1076016.4000000001 

626456.4328125003
1076016.4000000001
Gurobi Optimizer version 9.0.2 build v9.0.2rc0 (win64)
Optimize a model with 150 rows, 2550 columns and 7550 nonzeros
Model fingerprint: 0xe4208379
Coefficient statistics:
  Matrix range     [1e+00, 1e+00]
  Objective ra

       0    0.0000000e+00   7.214625e+03   0.000000e+00      0s
      58    7.2259525e+05   0.000000e+00   0.000000e+00      0s

Solved in 58 iterations and 0.01 seconds
Optimal objective  7.225952500e+05
Current LB:  1099532.7500000005 

760743.6564748603
1099532.7500000005
Gurobi Optimizer version 9.0.2 build v9.0.2rc0 (win64)
Optimize a model with 150 rows, 2550 columns and 7550 nonzeros
Model fingerprint: 0x4c54472b
Coefficient statistics:
  Matrix range     [1e+00, 1e+00]
  Objective range  [1e+00, 4e+04]
  Bounds range     [0e+00, 0e+00]
  RHS range        [3e+01, 1e+04]
Presolve removed 75 rows and 1250 columns
Presolve time: 0.01s
Presolved: 75 rows, 1300 columns, 2550 nonzeros

Iteration    Objective       Primal Inf.    Dual Inf.      Time
       0    0.0000000e+00   7.214625e+03   0.000000e+00      0s
      60    7.3000036e+05   0.000000e+00   0.000000e+00      0s

Solved in 60 iterations and 0.01 seconds
Optimal objective  7.300003625e+05
Current LB:  1102282.7500000002 

7

  Objective range  [1e+00, 4e+04]
  Bounds range     [0e+00, 0e+00]
  RHS range        [3e+01, 1e+04]
Presolve removed 82 rows and 1600 columns
Presolve time: 0.01s
Presolved: 68 rows, 950 columns, 1850 nonzeros

Iteration    Objective       Primal Inf.    Dual Inf.      Time
       0    0.0000000e+00   7.214625e+03   0.000000e+00      0s
      79    8.2098354e+05   0.000000e+00   0.000000e+00      0s

Solved in 79 iterations and 0.02 seconds
Optimal objective  8.209835375e+05
Current LB:  1100028.187499999 

797689.2928157763
1100028.187499999
Gurobi Optimizer version 9.0.2 build v9.0.2rc0 (win64)
Optimize a model with 150 rows, 2550 columns and 7550 nonzeros
Model fingerprint: 0x91c2e422
Coefficient statistics:
  Matrix range     [1e+00, 1e+00]
  Objective range  [1e+00, 4e+04]
  Bounds range     [0e+00, 0e+00]
  RHS range        [3e+01, 1e+04]
Presolve removed 80 rows and 1500 columns
Presolve time: 0.01s
Presolved: 70 rows, 1050 columns, 2050 nonzeros

Iteration    Objective       

AttributeError: Unable to retrieve attribute 'x'

...

Current LB:  942938.4375000001 

876624.1624086379
942938.4375000001
Gurobi Optimizer version 9.0.2 build v9.0.2rc0 (win64)
Optimize a model with 150 rows, 2550 columns and 7550 nonzeros
Model fingerprint: 0xbcde9549
Coefficient statistics:
  Matrix range     [1e+00, 1e+00]
  Objective range  [1e+00, 4e+04]
  Bounds range     [0e+00, 0e+00]
  RHS range        [3e+01, 1e+04]
Presolve removed 80 rows and 1500 columns
Presolve time: 0.01s
Presolved: 70 rows, 1050 columns, 2050 nonzeros

Iteration    Objective       Primal Inf.    Dual Inf.      Time
       0    0.0000000e+00   7.214625e+03   0.000000e+00      0s
      68    7.6604401e+05   0.000000e+00   0.000000e+00      0s

Solved in 68 iterations and 0.01 seconds
Optimal objective  7.660440125e+05
Current LB:  943473.7125000001 

876624.1624086379
943473.7125000001
Gurobi Optimizer version 9.0.2 build v9.0.2rc0 (win64)
Optimize a model with 150 rows, 2550 columns and 7550 nonzeros
Model fingerprint: 0xe811bba6
Coefficient statistics:
 


Solved in 61 iterations and 0.01 seconds
Optimal objective  7.808826000e+05
 316655 220581 956522.545   71    1 966333.824 876637.129  9.28%   9.1 1788s
Current LB:  964970.4000000001 

876637.1285407683
964970.4000000001
Gurobi Optimizer version 9.0.2 build v9.0.2rc0 (win64)
Optimize a model with 150 rows, 2550 columns and 7550 nonzeros
Model fingerprint: 0x3425fc35
Coefficient statistics:
  Matrix range     [1e+00, 1e+00]
  Objective range  [1e+00, 4e+04]
  Bounds range     [0e+00, 0e+00]
  RHS range        [3e+01, 1e+04]
Presolve removed 83 rows and 1650 columns
Presolve time: 0.01s
Presolved: 67 rows, 900 columns, 1750 nonzeros

Iteration    Objective       Primal Inf.    Dual Inf.      Time
       0    0.0000000e+00   7.214625e+03   0.000000e+00      0s
      61    7.7524336e+05   0.000000e+00   0.000000e+00      0s

Solved in 61 iterations and 0.01 seconds
Optimal objective  7.752433625e+05
Current LB:  960716.6125000006 

876642.5272582158
960716.6125000006
Gurobi Optimizer ver

       0    0.0000000e+00   7.214625e+03   0.000000e+00      0s
      59    7.5261634e+05   0.000000e+00   0.000000e+00      0s

Solved in 59 iterations and 0.01 seconds
Optimal objective  7.526163375e+05
Current LB:  944750.9375 

876649.1117594086
944750.9375
Gurobi Optimizer version 9.0.2 build v9.0.2rc0 (win64)
Optimize a model with 150 rows, 2550 columns and 7550 nonzeros
Model fingerprint: 0xfee771c6
Coefficient statistics:
  Matrix range     [1e+00, 1e+00]
  Objective range  [1e+00, 4e+04]
  Bounds range     [0e+00, 0e+00]
  RHS range        [3e+01, 1e+04]
Presolve removed 82 rows and 1600 columns
Presolve time: 0.01s
Presolved: 68 rows, 950 columns, 1850 nonzeros

Iteration    Objective       Primal Inf.    Dual Inf.      Time
       0    0.0000000e+00   7.283500e+03   0.000000e+00      0s
      79    8.0283082e+05   0.000000e+00   0.000000e+00      0s

Solved in 79 iterations and 0.01 seconds
Optimal objective  8.028308250e+05
Current LB:  963450.3625000002 

876655.0920880587

Presolve removed 79 rows and 1450 columns
Presolve time: 0.01s
Presolved: 71 rows, 1100 columns, 2150 nonzeros

Iteration    Objective       Primal Inf.    Dual Inf.      Time
       0    0.0000000e+00   7.214625e+03   0.000000e+00      0s
      62    7.3630959e+05   0.000000e+00   0.000000e+00      0s

Solved in 62 iterations and 0.01 seconds
Optimal objective  7.363095875e+05
Current LB:  958824.6374999995 

876666.508206199
958824.6374999995
Gurobi Optimizer version 9.0.2 build v9.0.2rc0 (win64)
Optimize a model with 150 rows, 2550 columns and 7550 nonzeros
Model fingerprint: 0x07216941
Coefficient statistics:
  Matrix range     [1e+00, 1e+00]
  Objective range  [1e+00, 4e+04]
  Bounds range     [0e+00, 0e+00]
  RHS range        [3e+01, 1e+04]
Presolve removed 81 rows and 1550 columns
Presolve time: 0.01s
Presolved: 69 rows, 1000 columns, 1950 nonzeros

Iteration    Objective       Primal Inf.    Dual Inf.      Time
       0    0.0000000e+00   7.214625e+03   0.000000e+00      0s
   

  Objective range  [1e+00, 4e+04]
  Bounds range     [0e+00, 0e+00]
  RHS range        [3e+01, 1e+04]
Presolve removed 82 rows and 1600 columns
Presolve time: 0.01s
Presolved: 68 rows, 950 columns, 1850 nonzeros

Iteration    Objective       Primal Inf.    Dual Inf.      Time
       0    0.0000000e+00   7.214625e+03   0.000000e+00      0s
      65    7.5046844e+05   0.000000e+00   0.000000e+00      0s

Solved in 65 iterations and 0.01 seconds
Optimal objective  7.504684375e+05
 318087 221313     cutoff   69      966333.824 876684.637  9.28%   9.1 1800s
Current LB:  946157.3749999995 

876685.2489745156
946157.3749999995
Gurobi Optimizer version 9.0.2 build v9.0.2rc0 (win64)
Optimize a model with 150 rows, 2550 columns and 7550 nonzeros
Model fingerprint: 0x2f537dbe
Coefficient statistics:
  Matrix range     [1e+00, 1e+00]
  Objective range  [1e+00, 4e+04]
  Bounds range     [0e+00, 0e+00]
  RHS range        [3e+01, 1e+04]
Presolve removed 80 rows and 1500 columns
Presolve time: 0.01s
P

In [12]:
#Number of open warehouses
sum(round(y[i].x) for i in y.keys())

25

In [13]:
#resolve transportation problem with fixed y obtained from Benders

In [14]:
y0 = [round(y[i].x) for i in y.keys()]

In [15]:
model0 = gp.Model()
x0 = {}
for i in range(locations):
    for j in range(customers):
        x0[i,j] = model0.addVar(obj=varcost[i][j])

#demand constraint
demand_constr = {} 
for j in range(customers):
    demand_constr[j] = model0.addConstr(sum(x0[i,j] for i in range(locations)) >= demand[j])
        
#capacity constraint
cap_constr = {}
for i in range(locations):
    cap_constr[i] = model0.addConstr(sum(x0[i,j] for j in range(customers)) <= capacity[i])

#logical constraint
log_constr = {}
for i in range(locations):
    log_constr[i] = model0.addConstr(sum(x0[i,j] for j in range(customers)) <= y0[i] * sum(demand))

model0.optimize()

print("Objective: " + str(model0.objVal))

print("Solution:")
import pandas as pd
index = ['Source ' + str(x+1) for x in range(locations)]
columns = ['Customer ' + str(x+1) for x in range(customers)]

solution = pd.DataFrame(index=index, columns=columns)

for i in range(locations):
    for j in range(customers):
        solution.iloc[i,j] = x0[i,j].x

print(solution)

Gurobi Optimizer version 9.0.2 build v9.0.2rc0 (win64)
Optimize a model with 150 rows, 2500 columns and 7500 nonzeros
Model fingerprint: 0xdc3e5fcc
Coefficient statistics:
  Matrix range     [1e+00, 1e+00]
  Objective range  [1e+00, 1e+02]
  Bounds range     [0e+00, 0e+00]
  RHS range        [3e+01, 6e+04]
Presolve removed 75 rows and 1250 columns
Presolve time: 0.01s
Presolved: 75 rows, 1250 columns, 2500 nonzeros

Iteration    Objective       Primal Inf.    Dual Inf.      Time
       0    0.0000000e+00   7.214625e+03   0.000000e+00      0s
      59    7.4083421e+05   0.000000e+00   0.000000e+00      0s

Solved in 59 iterations and 0.02 seconds
Optimal objective  7.408342125e+05
Objective: 740834.2125
Solution:
           Customer 1  Customer 2  Customer 3  Customer 4  Customer 5  \
Source 1          146           0           0           0           0   
Source 2            0           0           0           0           0   
Source 3            0           0         672           0  

In [16]:
#Total cost including fixed and transportation cost
model0.objVal+sum([y0[i]*fixcost[i] for i in range(locations)])

1160834.2125